# Text as Data

This notebook implements a similar granular approach as used on my midterm. Text is interpreted as data to control the parameters of a granular patch with respect to time.

In [11]:
import re
import signalflow as sf
import numpy as np
import IPython

In [5]:
means = dict([(chr(c), (c - 97) / 26) for c in range(97, 123)])


def char_to_val(c):
    # map a-z to X ~ N(posn. / 26, 0.2)
    if c in means:
        return np.random.normal(means[c], 0.2)
    return 0


def string_to_list(src):
    # string to a list of RVs as in above fn
    lst = []
    src = src.lower()
    for c in src:
        lst.append(char_to_val(c))
    return lst

In [8]:
if 'graph' in locals():
    graph.destroy()

graph = sf.AudioGraph(output_device=sf.AudioOut_Dummy(2))

### Prompt

Input text data prompt here:

In [1]:
# text to use as control
prompt = "Use this text to parameterize the patch"

# duration of one text cycle, sec
dur = 20

# input file path
src = "../sounds-1/overfit.wav"

In [131]:
dst = "out.wav"

out_buf = sf.Buffer(2, int(graph.sample_rate * dur))
in_buf = sf.Buffer(src)

ctrl_buf = sf.Buffer(string_to_list(prompt))
ctrl = sf.Wavetable(ctrl_buf, 1 / dur)

grain_rate = sf.Abs(sf.Sin(ctrl / 2 * np.pi * 4)) * 100 + 1e-3 + 4
pan_lvl = sf.Cos(ctrl * 2 * np.pi) ** 2
dur_lvl = ctrl ** 2 * 5
rate = sf.Round(ctrl * 2) * 0.5 + 0.5
rate *= 0.25

grain_clock = sf.RandomImpulse(grain_rate * dur * 0.5)
grain_pan = sf.RandomUniform(-1 * pan_lvl, pan_lvl, clock=grain_clock)
grain_dur = sf.RandomUniform(1 / grain_rate, 20 / grain_rate, clock=grain_clock)
grain_pos = ctrl * in_buf.duration

grain_window = sf.EnvelopeBuffer("triangle")

grains = sf.Granulator(in_buf, grain_clock, pan=grain_pan,
                       pos=grain_pos, rate=0.5, duration=grain_dur)
grains.set_buffer("envelope", grain_window)
grains += sf.Granulator(in_buf, grain_clock, pan=grain_pan,
                       pos=grain_pos * 0.5, rate=play_rate, duration=grain_dur) * 0.25


graph.play(grains * sf.DecibelsToAmplitude(-12))
graph.render_to_buffer(out_buf)
out_buf.save(dst)

graph.clear()

IPython.display.Audio(dst)

In [132]:
!mv out.wav ../text-data-sounds/s1-l5-overfit.wav